In [1]:
import sys
sys.path.append('/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/')
import os
import pickle
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from pathlib import Path
import yfinance as yf
import time
from datetime import timedelta, datetime
from systems.performance_reporter import PerformanceReporter

from systems.utils import MarketDataExtractor

In [2]:
market_data_extractor = MarketDataExtractor()
strategy_reporter = PerformanceReporter(market_data_extractor)

# Inputs

In [3]:
testname = 'c1ff5702001d336df59c25617f6918a3badf49c4944d32ed2d736f7c3d24f1fa_3' # Profits Reinvested & Margin Deployed @ 0.65 of 3.3x (exit on daily close, fill price is daily close)
save_folder = "/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/db/data/yahoo/1d"
test_folder_path = f'/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/db/vault/backtest_reports/{testname}'
indices = ["^DJI", "^IXIC", "^GSPC"]
starting_capital = 72463 * 3

In [4]:
# testname = '4c4f66a4e5697c5342a7e4dee1e145be8a85d133a7300ee6505a13895989a8e7' # Profits not Reinvested
backtest_output = strategy_reporter.load_backtest_output(test_folder_path)
open_orders = backtest_output['open_orders']
closed_orders = backtest_output['closed_orders']
config_dict = backtest_output['config_dict']
figures = []

In [5]:
#Processing Open order to make them close, and remove history
open_orders_list = strategy_reporter.clean_up_order_list(open_orders, drop_history=True)
#Processing Closed orders to remove history
closed_orders_list = strategy_reporter.clean_up_order_list(closed_orders, drop_history=True)
#Merge both orders
final_list = closed_orders_list + open_orders_list
# Step 2: Sort the filtered orders by exit order `filled_timestamp`
sorted_orders = sorted(final_list, key=lambda x: x[1]['filled_timestamp'])
# Step 3: Fetch the first and last `filled_timestamp` with buffer
start_date = sorted_orders[0][0]['filled_timestamp'] - timedelta(days=365)
end_date = sorted_orders[-1][-1]['filled_timestamp'] + timedelta(days=365)
# end_date = pd.Timestamp(datetime(2010, 1, 1))
# Current we are downloading csv file for below three index
index_data_dict = strategy_reporter.load_and_save_index_data(indices, start_date, end_date, save_folder)
rolling_window = int(max(60, (end_date - start_date).days / 20))
print(f"Analyzing Data with a rolling window of: {rolling_window} days")

Analyzing Data with a rolling window of: 310 days


### Equity Curve

In [6]:
# Drawdown analysis and Equity Curve should be on a day to day basis with open_position values updated on a daily basis based on the symbol_ltp mentioned on each order
trade_df_by_date = strategy_reporter.create_data_input_for_cumulative_returns_and_indices(final_list, index_data_dict, starting_capital)
# strategy_reporter.plot_cumulative_returns_and_indices(trade_df_by_date, index_data_dict)
figures.append(strategy_reporter.plot_cumulative_returns_and_indices(trade_df_by_date, index_data_dict))

In [7]:
# Log Curve of Cumulative Returns
trade_df_by_date['log_growth'] = np.log(trade_df_by_date['cumulative_return'])
log_index_data = np.log(index_data_dict['^IXIC']['close'])
figures.append(strategy_reporter.plot_cumulative_returns_log_scale(trade_df_by_date['log_growth'], log_index_data))

/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/systems/performance_reporter.py:516: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

/Users/vandanchopra/Vandan_Personal_Folder/CODE_STUFF/Projects/mathematricks/systems/performance_reporter.py:517: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`



# Plot Rolling charts

#### Sharpe Ratio

In [8]:
account_value = trade_df_by_date['account_value']
index_name = '^IXIC'
index_value = index_data_dict[index_name]['close']
risk_free_rate=0.0415
# rename 'close' to '^IXIC' in index_value
index_value = index_value.rename(index_name)
rolling_sharpe, rolling_sharpe_index, absolute_sharpe_ratio, absolute_sharpe_ratio_index = strategy_reporter.calculate_rolling_sharpe_ratio(account_value, index_value, risk_free_rate=risk_free_rate, window=rolling_window)
figures.append(strategy_reporter.plot_rolling_sharpe_ratio(rolling_sharpe, rolling_sharpe_index, absolute_sharpe_ratio, absolute_sharpe_ratio_index, risk_free_rate, window=rolling_window))

### Rolling Win Percentage

In [9]:
trade_df_by_order = strategy_reporter.prepare_trade_data_df_by_order(final_list)
# figures.append(strategy_reporter.plot_rolling_win_percentage(trade_df_by_order, index_data_dict, window=rolling_window))
figures.append(strategy_reporter.plot_rolling_win_percentage(trade_df_by_order, index_data_dict, window=rolling_window))

### Rolling Risk Reward Ratio

In [10]:
rolling_risk_reward_ratio, rolling_risk_reward_ratio_long, rolling_risk_reward_ratio_short = strategy_reporter.calculate_rolling_risk_reward_ratio(trade_df_by_order, window=rolling_window)
figures.append(strategy_reporter.plot_rolling_risk_reward_ratio(rolling_risk_reward_ratio, rolling_risk_reward_ratio_long, rolling_risk_reward_ratio_short, rolling_window, index_data_dict))

### Drawdown Analysis

In [11]:
trade_df_by_date_drawdown = strategy_reporter.calculate_drawdowns(trade_df_by_date)
figures.append(strategy_reporter.plot_drawdown(trade_df_by_date_drawdown, index_data_dict))

### Plot Trades of a Single Asset

In [12]:
from pprint import pprint
# Add order_num to the final_list
for order_num, order in enumerate(final_list):
    for i in range(len(order)):
        order[i]['order_num'] = order_num

# Get list of all the symbols in final_list
all_symbols = list(set([x[1]['symbol'] for x in final_list]))
# from pprint import pprint
pprint(str(all_symbols))

("['HPQ', 'TEL', 'BP', 'CSX', 'WEC', 'SRE', 'SHOP', 'MPLX', 'LEN', 'FITB', "
 "'AXP', 'CHTR', 'RBLX', 'SU', 'TCOM', 'TFC', 'GWW', 'BX', 'NXPI', 'SAN', "
 "'MAR', 'OWL', 'C', 'ASML', 'CP', 'APD', 'BKR', 'ITUB', 'VZ', 'UL', 'T', "
 "'CM', 'MSI', 'GSK', 'CUK', 'PBR', 'INTC', 'NSC', 'BMY', 'PRU', 'CSGP', "
 "'SAP', 'ABEV', 'NTES', 'BCS', 'ALNY', 'VEEV', 'GD', 'INTU', 'CRM', 'BLK', "
 "'FICO', 'ETR', 'VRSK', 'HIG', 'KVUE', 'ABNB', 'MLM', 'CTVA', 'FDX', 'VRT', "
 "'PEG', 'ING', 'APH', 'INFY', 'MS', 'ANET', 'HCA', 'AMX', 'FCNCA', 'CCL', "
 "'ICE', 'UAL', 'MUFG', 'IBN', 'PDD', 'IMO', 'SLB', 'XOM', 'GE', 'AMD', 'BHP', "
 "'AXON', 'DELL', 'EQNR', 'TEAM', 'TDG', 'UPS', 'CTAS', 'CDNS', 'CAT', 'HWM', "
 "'ONON', 'IBM', 'KHC', 'DE', 'PANW', 'DUK', 'URI', 'TTWO', 'WMB', 'STLA', "
 "'CRWD', 'MSFT', 'ET', 'SO', 'FMX', 'SPOT', 'AMZN', 'LMT', 'CCEP', 'MA', "
 "'HUM', 'GRMN', 'AJG', 'ARGX', 'GLW', 'BSBR', 'AMT', 'VMC', 'EOG', 'HDB', "
 "'BABA', 'WAB', 'O', 'DB', 'V', 'NU', 'MET', 'PGR', 'TSM', 'WM', 'COF'

In [13]:
# Add order_num to the final_list
for order_num, order in enumerate(open_orders_list):
    for i in range(len(order)):
        order[i]['order_num'] = order_num

# Get list of all the symbols in final_list
open_symbols = list(set([x[1]['symbol'] for x in open_orders_list]))
from pprint import pprint
pprint(str(open_symbols))

("['ANET', 'JCI', 'PDD', 'SE', 'VST', 'UBS', 'AMGN', 'VRT', 'FICO', 'ZS', "
 "'ALL', 'MSTR', 'HSY', 'DELL', 'CRWD']")


In [14]:
import random
symbol = random.choice(all_symbols)
print({'symbol':symbol})
if symbol in all_symbols:
    strategy_reporter.process_and_plot_orders(final_list, symbol, save_folder)
else:
    print(f"Symbol {symbol} not found in the final list of orders")

{'symbol': 'MS'}


In [15]:
count = 16
pnl = ((final_list[count][-1]['fill_price'] - final_list[count][0]['fill_price'])/final_list[count][0]['fill_price'])*100

In [16]:
closed_orders[count][0]['symbol_ltp']

{'2009-01-12 23:59:59+00:00': 28.15}

In [17]:
aligned_positive = []
aligned_negative = []
misaligned_positive = []
misaligned_negative = []
neutral_positive = []
neutral_negative = []

for count, closed_order in enumerate(final_list):
    order_direction = final_list[count][0]['orderDirection']
    if order_direction == 'BUY':
        pnl = ((final_list[count][-1]['fill_price'] - final_list[count][0]['fill_price'])/final_list[count][0]['fill_price'])*100
    else:
        pnl = ((final_list[count][0]['fill_price'] - final_list[count][-1]['fill_price'])/final_list[count][-1]['fill_price'])*100

    decision_matrix_df =  final_list[count][0]['decision_matrix']
    # regime_int = final_list[count][0]['decision_matrix'].iloc[0]['market_regime']
    
    regime_array = np.array([decision_matrix_df[decision_matrix_df['position_temp'] == 1].shape[0], decision_matrix_df[decision_matrix_df['position_temp'] == 0].shape[0], decision_matrix_df[decision_matrix_df['position_temp'] == -1].shape[0]])
    # find the index of the maximum value in the regime_array
    regime = np.argmax(regime_array)
    regime_int = 1 if regime == 0 else 0 if regime == 1 else -1
    
    if pnl > 0:
        if (order_direction == 'BUY' and regime_int == 1) or (order_direction == 'SELL' and regime_int == -1):
            aligned_positive.append(closed_order)
        elif regime_int == 0:
            neutral_positive.append(closed_order)
        else:
            misaligned_positive.append(closed_order)
            
    elif pnl < 0:
        if (order_direction == 'BUY' and regime_int == 1) or (order_direction == 'SELL' and regime_int == -1):
            aligned_negative.append(closed_order)
        elif regime_int == 0:
            neutral_negative.append(closed_order)
            # print({'order_direction':order_direction, 'pnl':pnl, 'regime_int':regime_int})
        else:
            misaligned_negative.append(closed_order)
            

In [18]:
print({'aligned_positive':len(aligned_positive), 'aligned_negative':len(aligned_negative), 'neutral_positive':len(neutral_positive), 'neutral_negative':len(neutral_negative), 'misaligned_positive':len(misaligned_positive), 'misaligned_negative':len(misaligned_negative)})

{'aligned_positive': 617, 'aligned_negative': 1491, 'neutral_positive': 2671, 'neutral_negative': 5951, 'misaligned_positive': 0, 'misaligned_negative': 0}


In [19]:
print(f'Win Ratio: Aligned: {(len(aligned_positive)/(len(aligned_negative) + len(aligned_positive)))}')
print(f'Win Ratio: MisAligned: {(len(misaligned_positive)/(len(misaligned_negative) + len(misaligned_positive)))}')
print(f'Win Ratio: Neutral: {(len(neutral_positive)/(len(neutral_negative) + len(neutral_positive)))}')
print(f'Win Ratio: Overall: {(len(aligned_positive) + len(misaligned_positive) + len(neutral_positive))/len(closed_orders)}')
print(f'Win Ratio: Aligned + Neutral: {(len(aligned_positive) + len(neutral_positive))/(len(neutral_negative) + len(neutral_positive) + len(aligned_positive) + len(aligned_negative))}')


Win Ratio: Aligned: 0.2926944971537002


ZeroDivisionError: division by zero

In [ ]:
decision_matrix_df

In [ ]:
for x in range(1,1000):
    order = neutral_positive[x]
    order_direction = order[0]['orderDirection']
    symbol = order[0]['symbol']
    if order_direction == 'BUY':
        pnl = ((final_list[count][-1]['fill_price'] - order[0]['fill_price'])/order[0]['fill_price'])*100
    else:
        pnl = ((final_list[count][0]['fill_price'] - order[-1]['fill_price'])/order[-1]['fill_price'])*100
        
    print({'Symbol': symbol, 'PnL': pnl, 'Order Direction': order_direction})
    
    

In [ ]:
decision_matrix = None
for x in range(1,1000):
    if x > 39:
        regime = neutral_positive[x][0]['decision_matrix'].iloc[0]['market_regime']
        if regime == 0:
            decision_matrix = neutral_positive[x][0]['decision_matrix']
            break

In [ ]:
decision_matrix

# Save all Figures to HTML

In [ ]:
strategy_reporter.save_to_html_file(figures, testname, test_folder_path, strategies=config_dict['strategies'])